**Monture de Google Drive**

Cela monte le Google Drive de l'utilisateur afin de pouvoir accéder aux fichiers nécessaires stockés dans le drive.

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


**Chargement et Affichage des Images**

Ici, les premières 5 images sont chargées et affichées à l'aide de cv2 et matplotlib.

In [ ]:
import os
import cv2
import matplotlib.pyplot as plt
import numpy as np

chemin_basededonnees = "/content/drive/My Drive/projet_datamining/train"

images = []
labels = []

# Charger et prétraiter les images redimensionnées
for nom_image in os.listdir(chemin_basededonnees):
    # Charger l'image en couleur
    image = cv2.imread(os.path.join(chemin_basededonnees, nom_image))

    # Ajouter l'image redimensionnée à la liste
    images.append(image)

    # Stopper après avoir chargé 5 images pour afficher le "head"
    if len(images) == 5:
        break

# Convertir les listes en tableaux numpy
images = np.array(images)

print("Images shape:", images.shape)

# Afficher les premières images redimensionnées
nb_images_total = len(images)
nb_lignes = (nb_images_total - 1) // 5 + 1  # 5 images par ligne
nb_colonnes = min(5, nb_images_total)  # Maximum 5 images par ligne

plt.figure(figsize=(20, 20))
for i, image in enumerate(images):
    plt.subplot(nb_lignes, nb_colonnes, i+1)
    plt.imshow(cv2.cvtColor(image, cv2.COLOR_BGR2RGB))
    plt.axis('off')  # Masquer les axes
plt.show()

Images shape: (5, 700, 700, 3)


**Conversion du Fichier NDJSON en Format COCO**

Cette fonction convertit les annotations du format NDJSON en format COCO, un format standard pour les annotations d'images.

In [ ]:
import json

def ndjson_to_coco(ndjson_file, coco_file):
    with open(ndjson_file, 'r') as f:
        lines = f.readlines()

    data = [json.loads(line) for line in lines]

    coco_format = {
        "images": [],
        "annotations": [],
        "categories": []
    }

    # Initialisation des catégories
    category_map = {"fragmented": 1, "not_fragmented": 2}
    coco_format['categories'].append({"id": 1, "name": "fragmented"})
    coco_format['categories'].append({"id": 2, "name": "not_fragmented"})

    annotation_id = 1
    for image_id, entry in enumerate(data):
        image_info = entry['data_row']
        media_attributes = entry['media_attributes']

        coco_format["images"].append({
            "id": image_id,
            "file_name": image_info["external_id"],
            "width": media_attributes["width"],
            "height": media_attributes["height"]
        })

        project_info = entry['projects']
        for project_key, project_value in project_info.items():
            for label in project_value['labels']:
                annotations = label['annotations']['objects']
                for annotation in annotations:
                    bbox = annotation['bounding_box']
                    coco_format["annotations"].append({
                        "id": annotation_id,
                        "image_id": image_id,
                        "category_id": category_map[annotation["value"]],
                        "bbox": [bbox["left"], bbox["top"], bbox["width"], bbox["height"]],
                        "area": bbox["width"] * bbox["height"],
                        "iscrowd": 0
                    })
                    annotation_id += 1

    with open(coco_file, 'w') as f:
        json.dump(coco_format, f)

# Chemin vers le fichier NDJSON et le fichier COCO de sortie
ndjson_file = '/content/drive/My Drive/projet_datamining/train&mixed.ndjson'
coco_file = '/content/drive/My Drive/projet_datamining/train&mixed_coco.json'

# Conversion
ndjson_to_coco(ndjson_file, coco_file)

print("Conversion terminée. Les annotations sont enregistrées dans", coco_file)


Conversion terminée. Les annotations sont enregistrées dans /content/drive/My Drive/projet_datamining/train&mixed_coco.json


**Chargement des données**

Le code que vous avez partagé permet de charger des images et leurs annotations à partir de fichiers COCO, puis de créer un DataLoader PyTorch pour ces données.



*   Chargement des annotations COCO :
      Cette fonction lit le fichier COCO JSON et retourne les données sous forme de dictionnaire.

*   Extraction des annotations d'une image :
      Cette fonction filtre les annotations pour ne conserver que celles associées à l'ID de l'image spécifiée.

*   Chargement et transformation des images : Cette fonction lit l'image à partir du chemin donné, la convertit en format RGB, puis la transforme en tenseur PyTorch.

*    Création du DataLoader :


                1.   create_data_loader : Charge les annotations COCO et les images correspondantes, crée une liste de tuples (image, annotations) et retourne un DataLoader PyTorch qui charge les données en lots (batches).
                2.   Les images sont transformées en tenseurs PyTorch et les annotations sont filtrées pour chaque image.
                3.   collate_fn=lambda x: tuple(zip(*x)) : Permet de combiner les images et les annotations en lots.

*     Définition des chemins et création du DataLoader :


                1.   image_dir : Répertoire contenant les images.
                2.   coco_file : Fichier COCO JSON contenant les annotations.
                3.   create_data_loader : Crée le DataLoader avec les images et annotations spécifiées.





In [ ]:
import torchvision.transforms as transforms
import torch.utils.data as data
import torchvision

def load_coco_annotations(coco_file):
    with open(coco_file, 'r') as f:
        coco_data = json.load(f)
    return coco_data

def get_image_annotations(image_id, annotations):
    return [anno for anno in annotations if anno['image_id'] == image_id]

def load_image(img_path):
    img = cv2.imread(img_path, cv2.IMREAD_COLOR)  # Lire les images en couleur
    if img is None:
        raise FileNotFoundError(f"Image not found: {img_path}")
    img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
    img = transforms.ToTensor()(img)
    return img

def create_data_loader(image_dir, coco_file, batch_size=2):
    coco_data = load_coco_annotations(coco_file)
    images = coco_data['images']
    annotations = coco_data['annotations']

    dataset = []
    for img_info in images:
        img_path = os.path.join(image_dir, img_info['file_name'])
        if not os.path.exists(img_path):
            print(f"Warning: Image {img_path} does not exist.")
            continue
        img = load_image(img_path)
        annos = get_image_annotations(img_info['id'], annotations)
        dataset.append((img, annos))

    data_loader = data.DataLoader(dataset, batch_size=batch_size, shuffle=True, collate_fn=lambda x: tuple(zip(*x)))
    return data_loader

image_dir = "/content/drive/My Drive/projet_datamining/train"
coco_file = "/content/drive/My Drive/projet_datamining/train&mixed_coco.json"

**Chargement et Affichage des Annotations COCO**

Ce code charge et affiche le contenu du fichier COCO pour vérifier les annotations.



In [ ]:
with open(coco_file, "r") as fichier:
    donnees_coco = json.load(fichier)

# Afficher le contenu du fichier COCO
print(json.dumps(donnees_coco, indent=4))

{
    "images": [
        {
            "id": 0,
            "file_name": "1.png",
            "width": 700,
            "height": 700
        },
        {
            "id": 1,
            "file_name": "2.png",
            "width": 700,
            "height": 700
        },
        {
            "id": 2,
            "file_name": "3.png",
            "width": 700,
            "height": 700
        },
        {
            "id": 3,
            "file_name": "4.png",
            "width": 700,
            "height": 700
        },
        {
            "id": 4,
            "file_name": "5.png",
            "width": 700,
            "height": 700
        },
        {
            "id": 5,
            "file_name": "6.png",
            "width": 700,
            "height": 700
        },
        {
            "id": 6,
            "file_name": "7.png",
            "width": 700,
            "height": 700
        },
        {
            "id": 7,
            "file_name": "8.png",
            "width": 

**Chargement du modèle pré-entraîné**

Cette ligne de code crée une instance du modèle Faster R-CNN avec les poids pré-entraînés sur le dataset COCO



*   fasterrcnn_resnet50_fpn : C'est une fonction de torchvision qui renvoie une instance du modèle Faster R-CNN avec un backbone ResNet-50 et un Feature Pyramid Network.

*   pretrained=False : Indique que nous ne souhaitons pas utiliser les poids par défaut fournis avec la bibliothèque torchvision. Au lieu de cela, nous allons spécifier les poids que nous voulons utiliser via l'argument weights.

*    weights=FasterRCNN_ResNet50_FPN_Weights.COCO_V1 : Spécifie les poids pré-entraînés que nous souhaitons utiliser. FasterRCNN_ResNet50_FPN_Weights.COCO_V1 indique que nous utilisons les poids pré-entraînés sur le dataset COCO.


In [ ]:
from torchvision.models.detection import fasterrcnn_resnet50_fpn
from torchvision.models.detection.faster_rcnn import FasterRCNN_ResNet50_FPN_Weights

# Charger le modèle pré-entraîné
model = fasterrcnn_resnet50_fpn(pretrained=False, weights=FasterRCNN_ResNet50_FPN_Weights.COCO_V1)

Downloading: "https://download.pytorch.org/models/fasterrcnn_resnet50_fpn_coco-258fb6c6.pth" to /root/.cache/torch/hub/checkpoints/fasterrcnn_resnet50_fpn_coco-258fb6c6.pth
100%|██████████| 160M/160M [00:00<00:00, 183MB/s]


**Division des Données en Ensembles d'Entraînement et de Test**

Le code divise les annotations en ensembles d'entraînement et de test, puis les enregistre dans des fichiers séparés.



In [ ]:
import random

# Charger les annotations mises à jour
with open(ndjson_file, 'r') as f:
    updated_annotations = [json.loads(line) for line in f]

# Mélanger les annotations de manière aléatoire
random.shuffle(updated_annotations)

# Déterminer la taille de l'ensemble de test (par exemple, 20%)
test_size = int(0.2 * len(updated_annotations))

# Diviser les annotations en ensembles d'entraînement et de test
train_annotations = updated_annotations[test_size:]
test_annotations = updated_annotations[:test_size]

# Enregistrer les ensembles d'annotations dans des fichiers distincts
train_file = '/content/drive/My Drive/projet_datamining/train&mixed_train.ndjson'
test_file = '/content/drive/My Drive/projet_datamining/train&mixed_test.ndjson'

with open(train_file, 'w') as f:
    for annotation in train_annotations:
        json.dump(annotation, f)
        f.write('\n')

with open(test_file, 'w') as f:
    for annotation in test_annotations:
        json.dump(annotation, f)
        f.write('\n')

print("Ensemble de données divisé en ensembles d'entraînement et de test.")


Ensemble de données divisé en ensembles d'entraînement et de test.


**Chargement des Annotations et Affichage des Statistiques**

Ce code compte et affiche le nombre de cellules fragmentées et non fragmentées dans les annotations dans la partie de Training.


In [ ]:
import json

# Chemin vers le fichier NDJSON
file_path = '/content/drive/My Drive/projet_datamining/train&mixed_train.ndjson'

# Charger le fichier NDJSON
with open(file_path, 'r') as f:
    lignes = f.readlines()

# Initialisation des compteurs
count_fragmented = 0
count_not_fragmented = 0

# Parcours des lignes du fichier NDJSON
for ligne in lignes:
    annotation = json.loads(ligne)
    annotations = annotation['projects']['clwkvb637053c08y3e6xfgsz4']['labels'][0]['annotations']['objects']
    for obj in annotations:
        if obj['name'] == 'not_fragmented':
            count_not_fragmented += 1
        elif obj['name'] == 'fragmented':
            count_fragmented += 1

print(f"Nombre de cellules fragmentées: {count_fragmented}")
print(f"Nombre de cellules non fragmentées: {count_not_fragmented}")


Nombre de cellules fragmentées: 1842
Nombre de cellules non fragmentées: 1778


In [ ]:
def display_annotations(annotations_file):
    with open(annotations_file, 'r') as f:
        annotations = [json.loads(line) for line in f]
    for annotation in annotations:
        print(annotation)

train_annotations_file = '/content/drive/My Drive/projet_datamining/train&mixed_train.ndjson'
test_annotations_file = '/content/drive/My Drive/projet_datamining/train&mixed_test.ndjson'

print("Annotations d'entraînement:")
display_annotations(train_annotations_file)



Annotations d'entraînement:


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



{'data_row': {'id': 'clwkux4dc4h8w0707k5kxq706', 'external_id': '545.png', 'row_data': 'https://storage.labelbox.com/clwkt6lbw03kg07wq8w0rgo2u%2F3552392f-9d56-78a0-34cf-5ec1f5334721-545.png?Expires=1716725028609&KeyName=labelbox-assets-key-3&Signature=4cHAIDP9BulrLw_uDp5wtQu_KT4', 'details': {'dataset_id': 'clwkuc7wj003w070188ofbgax', 'dataset_name': 'dataset', 'created_at': '2024-05-24T15:49:00.790+00:00', 'updated_at': '2024-05-24T15:49:03.246+00:00', 'last_activity_at': '2024-05-25T00:07:08.573+00:00', 'created_by': 'brahim.zarhmir.m23@ump.ac.ma'}}, 'media_attributes': {'height': 700, 'width': 700, 'asset_type': 'image', 'mime_type': 'image/png', 'exif_rotation': '1'}, 'attachments': [], 'metadata_fields': [], 'projects': {'clwkvb637053c08y3e6xfgsz4': {'name': 'Train', 'labels': [{'label_kind': 'Default', 'version': '1.0.0', 'id': 'clwlcpgr602vu07fm6s0baxj2', 'label_details': {'created_at': '2024-05-25T00:07:08.000+00:00', 'updated_at': '2024-05-25T00:07:08.000+00:00', 'created_by':

In [ ]:
print("\nAnnotations de test:")
display_annotations(test_annotations_file)


Annotations de test:
{'data_row': {'id': 'clwkux4hv4hnl0707tl62flqz', 'external_id': '1074.png', 'row_data': 'https://storage.labelbox.com/clwkt6lbw03kg07wq8w0rgo2u%2F3d5065f6-7d20-909e-47b0-17817616c5ea-1074.png?Expires=1716725028186&KeyName=labelbox-assets-key-3&Signature=FX3P6KNcWGkOBUdMS4-6NQNUuUM', 'details': {'dataset_id': 'clwkuc7wj003w070188ofbgax', 'dataset_name': 'dataset', 'created_at': '2024-05-24T15:49:01.331+00:00', 'updated_at': '2024-05-24T15:49:07.452+00:00', 'last_activity_at': '2024-05-25T09:52:20.652+00:00', 'created_by': 'brahim.zarhmir.m23@ump.ac.ma'}}, 'media_attributes': {'height': 700, 'width': 700, 'asset_type': 'image', 'mime_type': 'image/png', 'exif_rotation': '1'}, 'attachments': [], 'metadata_fields': [], 'projects': {'clwkvb637053c08y3e6xfgsz4': {'name': 'Train', 'labels': [{'label_kind': 'Default', 'version': '1.0.0', 'id': 'clwlxlxuj0j5v07i72rd5cojs', 'label_details': {'created_at': '2024-05-25T09:52:20.000+00:00', 'updated_at': '2024-05-25T09:52:20.0

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



**Création de DataLoader pour l'Entraînement et le Test**

Ces fonctions créent les DataLoaders pour l'entraînement et le test en utilisant les annotations divisées précédemment.

In [ ]:
import json
import os
import cv2
import torch.utils.data as data
import torchvision.transforms as transforms

def load_ndjson_file(file_path):
    data = []
    with open(file_path, 'r') as f:
        for line in f:
            data.append(json.loads(line))
    return data

def load_image(img_path):
    img = cv2.imread(img_path, cv2.IMREAD_COLOR)
    if img is None:
        raise FileNotFoundError(f"Image not found: {img_path}")
    img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
    img = transforms.ToTensor()(img)
    return img

def annotation_generator(annotations_file, image_dir, batch_size=32):
    annotations_data = load_ndjson_file(annotations_file)
    batch = []
    for annotation in annotations_data:
        img_path = os.path.join(image_dir, annotation['data_row']['external_id'])
        if not os.path.exists(img_path):
            print(f"Warning: Image {img_path} does not exist.")
            continue
        img = load_image(img_path)
        batch.append((img, annotation['projects']['clwkvb637053c08y3e6xfgsz4']['labels'][0]['annotations']['objects']))
        if len(batch) == batch_size:
            yield batch
            batch = []
    if batch:
        yield batch

class CustomDataset(data.Dataset):
    def __init__(self, annotations_file, image_dir, batch_size=32):
        self.annotations_file = annotations_file
        self.image_dir = image_dir
        self.batch_size = batch_size
        self.annotations_data = load_ndjson_file(annotations_file)

    def __len__(self):
        return len(self.annotations_data)

    def __getitem__(self, idx):
        annotation = self.annotations_data[idx]
        img_path = os.path.join(self.image_dir, annotation['data_row']['external_id'])
        if not os.path.exists(img_path):
            raise FileNotFoundError(f"Image {img_path} does not exist.")
        img = load_image(img_path)
        return img, annotation['projects']['clwkvb637053c08y3e6xfgsz4']['labels'][0]['annotations']['objects']

def create_data_loader(image_dir, annotations_file, batch_size=32):
    dataset = CustomDataset(annotations_file, image_dir, batch_size)
    data_loader = data.DataLoader(dataset, batch_size=batch_size, shuffle=True, collate_fn=lambda x: tuple(zip(*x)))
    return data_loader

image_dir = "/content/drive/My Drive/projet_datamining/train"
train_annotations_file = '/content/drive/My Drive/projet_datamining/train&mixed_train.ndjson'
test_annotations_file = '/content/drive/My Drive/projet_datamining/train&mixed_test.ndjson'

train_data_loader = create_data_loader(image_dir, train_annotations_file)
test_data_loader = create_data_loader(image_dir, test_annotations_file)


**Initialisation du Modèle et de l'Optimiseur**

Le modèle Faster R-CNN est initialisé sans pré-entraînement et un optimiseur SGD est configuré pour l'entraînement.

In [ ]:
import torchvision

# Initialiser un nouveau modèle Faster R-CNN sans pré-entraînement
model = torchvision.models.detection.fasterrcnn_resnet50_fpn(pretrained=False)

/usr/local/lib/python3.10/dist-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)
Downloading: "https://download.pytorch.org/models/resnet50-0676ba61.pth" to /root/.cache/torch/hub/checkpoints/resnet50-0676ba61.pth
100%|██████████| 97.8M/97.8M [00:00<00:00, 140MB/s]


In [ ]:
import torch
# Définir l'optimiseur
params = [p for p in model.parameters() if p.requires_grad]
optimizer = torch.optim.SGD(model.parameters(), lr=0.005, momentum=0.9, weight_decay=0.0005)

**Entraînement du Modèle**

Le modèle est entraîné pendant un certain nombre d'époques, et la perte moyenne pour chaque époque est affichée.

In [ ]:
import os
import json
import time
import torch
import torchvision
import numpy as np
import cv2
from PIL import Image
from torch.utils.data import DataLoader, Dataset
from torchvision.models.detection import fasterrcnn_resnet50_fpn, FasterRCNN_ResNet50_FPN_Weights
from torchvision.transforms import ToTensor

# Vérifiez si CUDA est disponible
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
print(f"Using device: {device}")

# Charger le modèle pré-entraîné
weights = FasterRCNN_ResNet50_FPN_Weights.COCO_V1
model = fasterrcnn_resnet50_fpn(weights=weights)
model.to(device)

# Définir l'optimiseur
params = [p for p in model.parameters() if p.requires_grad]
optimizer = torch.optim.SGD(params, lr=0.005, momentum=0.9, weight_decay=0.0005)

# Nombre d'époques
num_epochs = 20

class CustomDataset(Dataset):
    def __init__(self, image_dir, annotations_file):
        self.image_dir = image_dir
        self.annotations = self.load_ndjson_file(annotations_file)
        self.transforms = ToTensor()

    def __len__(self):
        return len(self.annotations)

    def __getitem__(self, idx):
        annotation = self.annotations[idx]
        img_path = os.path.join(self.image_dir, annotation['data_row']['external_id'])
        img = Image.open(img_path).convert("RGB")
        img = self.transforms(img)

        boxes = []
        labels = []
        for obj in annotation['projects']['clwkvb637053c08y3e6xfgsz4']['labels'][0]['annotations']['objects']:
            box = obj['bounding_box']
            boxes.append([box['left'], box['top'], box['left'] + box['width'], box['top'] + box['height']])

            # Encoder les labels avec les IDs de catégories COCO
            if obj['name'] == 'fragmented':
                labels.append(1)  # 1 pour fragmented
            elif obj['name'] == 'not_fragmented':
                labels.append(2)  # 2 pour not_fragmented

        target = {
            'boxes': torch.tensor(boxes, dtype=torch.float32),
            'labels': torch.tensor(labels, dtype=torch.int64)
        }

        return img, target

    def load_ndjson_file(self, file_path):
        with open(file_path, 'r') as f:
            return [json.loads(line) for line in f]

def collate_fn(batch):
    return tuple(zip(*batch))

# Optimisation du DataLoader
def create_data_loader(image_dir, annotations_file, batch_size=2, num_workers=2):
    dataset = CustomDataset(image_dir, annotations_file)
    data_loader = DataLoader(dataset, batch_size=batch_size, shuffle=True, num_workers=num_workers, collate_fn=collate_fn)
    return data_loader

# Définir les chemins
image_dir = "/content/drive/My Drive/projet_datamining/train"
train_annotations_file = '/content/drive/My Drive/projet_datamining/train&mixed_train.ndjson'

# Créer le DataLoader pour l'entraînement
train_data_loader = create_data_loader(image_dir, train_annotations_file, batch_size=2, num_workers=2)

# Entraînement du modèle
for epoch in range(num_epochs):
    start_time = time.time()
    model.train()
    epoch_loss = 0

    for batch_idx, (images, targets) in enumerate(train_data_loader):
        batch_start_time = time.time()

        # Déplacer les images vers le périphérique (CPU ou GPU)
        images = [image.to(device) for image in images]

        # Déplacer les cibles vers le périphérique (CPU ou GPU)
        targets = [{k: v.to(device) for k, v in t.items()} for t in targets]

        optimizer.zero_grad()

        # Calculer les pertes
        loss_dict = model(images, targets)
        losses = sum(loss for loss in loss_dict.values())

        # Backpropagation
        losses.backward()
        optimizer.step()

        epoch_loss += losses.item()

        batch_end_time = time.time()
        print(f"Epoch [{epoch+1}/{num_epochs}], Batch [{batch_idx+1}/{len(train_data_loader)}], Loss: {losses.item()}, Batch Time: {batch_end_time - batch_start_time:.2f}s")

    avg_epoch_loss = epoch_loss / len(train_data_loader)
    end_time = time.time()
    print(f"Epoch [{epoch+1}/{num_epochs}] completed in {end_time - start_time:.2f}s, Average Loss: {avg_epoch_loss:.4f}")

print("Entraînement terminé")


Streaming output truncated to the last 5000 lines.
Epoch [15/20], Batch [360/892], Loss: 0.0012635358143597841, Batch Time: 0.41s
Epoch [15/20], Batch [361/892], Loss: 0.09230717271566391, Batch Time: 0.40s
Epoch [15/20], Batch [362/892], Loss: 0.001282630255445838, Batch Time: 0.41s
Epoch [15/20], Batch [363/892], Loss: 0.001764237298630178, Batch Time: 0.40s
Epoch [15/20], Batch [364/892], Loss: 0.036540497094392776, Batch Time: 0.40s
Epoch [15/20], Batch [365/892], Loss: 0.04893078655004501, Batch Time: 0.40s
Epoch [15/20], Batch [366/892], Loss: 0.0008461990510113537, Batch Time: 0.40s
Epoch [15/20], Batch [367/892], Loss: 0.0006027045310474932, Batch Time: 0.40s
Epoch [15/20], Batch [368/892], Loss: 0.2403767853975296, Batch Time: 0.43s
Epoch [15/20], Batch [369/892], Loss: 0.11885743588209152, Batch Time: 0.40s
Epoch [15/20], Batch [370/892], Loss: 0.14556796848773956, Batch Time: 0.40s
Epoch [15/20], Batch [371/892], Loss: 0.030941475182771683, Batch Time: 0.40s
Epoch [15/20], B

**Sauvgardage du model**

In [ ]:
torch.save(model.state_dict(), '/content/drive/My Drive/projet_datamining/fasterrcnn_model.pth')

**Évaluation des Performances du Modèle**

Le modèle est évalué sur l'ensemble de test, et les métriques de performance (précision, rappel, F1-score) sont calculées et affichées.

In [ ]:
import torch
import torchvision
from sklearn.metrics import accuracy_score, recall_score, f1_score, confusion_matrix

# Charger le modèle et ses poids
model = torchvision.models.detection.fasterrcnn_resnet50_fpn(pretrained=True)
model.load_state_dict(torch.load('/content/drive/My Drive/projet_datamining/fasterrcnn_model.pth'))
model.eval()
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
model.to(device)

# Préparer le DataLoader pour l'ensemble de test
test_data_loader = create_data_loader(image_dir, test_annotations_file, batch_size=1, num_workers=2)

# Faire des prédictions sur l'ensemble de test et collecter les résultats
all_labels = []
all_preds = []

with torch.no_grad():
    for images, targets in test_data_loader:
        images = [image.to(device) for image in images]

        # Faire des prédictions
        outputs = model(images)

        for target, output in zip(targets, outputs):
            true_labels = target['labels'].cpu().numpy()
            all_labels.extend(true_labels)

            # Filtrer les prédictions avec un score de confiance élevé
            pred_labels = output['labels'].cpu().numpy()
            pred_scores = output['scores'].cpu().numpy()
            high_conf_preds = pred_labels[pred_scores > 0.5]  # Seulement les prédictions avec score > 0.5
            all_preds.extend(high_conf_preds)

# Assurez-vous que les listes all_labels et all_preds sont de la même longueur
min_len = min(len(all_labels), len(all_preds))
all_labels = all_labels[:min_len]
all_preds = all_preds[:min_len]

# Calculer la précision, le rappel, et la mesure F1 en tenant compte du nombre de prédictions effectives
accuracy = accuracy_score(all_labels, all_preds)
recall = recall_score(all_labels, all_preds, average='weighted')
f1 = f1_score(all_labels, all_preds, average='weighted')
conf_matrix = confusion_matrix(all_labels, all_preds)

print(f"Accuracy: {accuracy:.4f}")
print(f"Recall: {recall:.4f}")
print(f"F1 Score: {f1:.4f}")
print("Confusion Matrix:")
print(conf_matrix)


Accuracy: 0.5167
Recall: 0.5167
F1 Score: 0.5128
Confusion Matrix:
[[148 198]
 [135 208]]
